# Training Set Debugging with mlwhatif
To demonstrate the ... The pipeline is implemented using native constructs from the popular pandas and scikit-learn libraries.

In [1]:
from demo.feature_overview.demo_utils import display_paper_figure, display_demo_source_code
display_paper_figure()

Let us start by looking at the full pipeline source code.

In [3]:
import os
from mlwhatif.utils import get_project_root

DEMO_PY = os.path.join(str(get_project_root()), "demo", "dc_demo", "sneakers.py")
display_demo_source_code(DEMO_PY)

In this scenario, we realized that there are problems with respect to the `weight` attribute in the test data of the pipeline. Sometimes the weight is zero, in other cases the weight is unnaturally high. We now want to investigate how such errors might impact our pipeline.

To conduct our analyses, we do not need to rewrite this pipeline file, we can use it directly as input for mlwhatif.

We use two what-if analyses. The first one is `CleanLearn`. We want to try two different cleaning approaches for outliers on our test data, dropping and imputing outliers. In addition, we will use the what-if analysis `OperatorImpact` to understand the impact of certain operators in our pipeline, the standard scaling for `weight`, and the model.

The central entry point of mlwhatif is the `PipelineAnalyzer`. To use mlwhatif, we use it and pass it the path to the runnable version of the example pipeline. Here, we have the example pipeline in a healthcare.py file, but e.g., `.ipynb` jupyter notebook files are supported, too. Then, we define the set of what-if analyses we want mlwhatif to run. Then, we execute the pipeline. mlwhatif returns a `AnalysisResults` object, which contains the output of our what-if analyses. This API is very close to the mlinspect API, because the implementation uses mlinspect as a basis for its plan extraction.

In [4]:
from mlwhatif import PipelineAnalyzer
from example_pipelines.healthcare import custom_monkeypatching
from demo.dc_demo.demo_utils import TrainingSetDebugging
import warnings
warnings.filterwarnings('ignore')  # To keep the output readable


training_set_debugging = TrainingSetDebugging()

analysis_result = PipelineAnalyzer \
    .on_pipeline_from_py_file(DEMO_PY) \
    .add_what_if_analysis(training_set_debugging) \
    .add_custom_monkey_patching_module(custom_monkeypatching) \
    .execute()

debugging_report = analysis_result.analysis_to_result_reports[training_set_debugging]

2023-05-24 16:15:21 INFO  Running instrumented original pipeline...
2023-05-24 16:15:21 INFO  Importing libraries and monkey-patching them... (Imports are slow if not in sys.modules cache yet!)
2023-05-24 16:15:22 INFO  ---RUNTIME: Importing and monkey-patching took 505.36203384399414 ms
2023-05-24 16:15:23.751232: I tensorflow/core/platform/cpu_feature_guard.cc:142] This TensorFlow binary is optimized with oneAPI Deep Neural Network Library (oneDNN) to use the following CPU instructions in performance-critical operations:  AVX2 FMA
To enable them in other operations, rebuild TensorFlow with the appropriate compiler flags.
2023-05-24 16:15:23.966430: I tensorflow/compiler/mlir/mlir_graph_optimization_pass.cc:176] None of the MLIR Optimization Passes are enabled (registered 2)
2023-05-24 16:15:32 INFO  ---RUNTIME: Original pipeline execution took 10825.20604133606 ms (excluding imports and monkey-patching)
2023-05-24 16:15:32 INFO  Starting execution of 1 what-if analyses...
2023-05-24 

Let us start by looking at the report generated by the `cleanlearn` analysis. Each row in this pandas `DataFrame` corresponds to one pipeline variant executed by mlwhatif. In the first report column, we see a column from the original pipeline that was cleaned in this pipeline variant. In the second column, we see the type of error in the column. In the third column, we see the cleaning method tried in the variant. In the fourth column, we see the utility score of the variant.

In the first row, we see the output for the original pipeline.

Here, we find that both cleaning approaches improve the performance of our pipeline. Here, the outlier imputation strategy results in slightly higher scores then just dropping outliers.

In [5]:
debugging_report

corrupted_column     error  cleaning_method  accuracy_score_L77
0             None      None             None            0.953782
1             None  mislabel  cleanlab_delete            0.970588
2             None  mislabel  cleanlab_update            0.953782
3             None  mislabel   shapley_delete            0.962185
4             None  mislabel   shapley_update            0.957983

## Further reading

In this demo notebook, we used relatively simple what-if analyses for demonstration purposes and replicated the simple example from the paper. We also prepared another demonstration notebook for advanced users already fully familiar with the ideas behind our approach. To get a full overview over our real, more powerful what-if analyses (as proposed by different papers) and a full overview over the functionality of mlwhatif, we refer to [this second notebook](../advanced_features/advanced_features.ipynb).